In [1]:
import pandas as pd
import geopandas as gpd
import shapely
import ee, geemap
import json

In [2]:
ee.Authenticate()
ee.Initialize()

In [3]:
CLOUD_THRESHOLD = 20
PRE_FIRE_DAYS = 60  # Days before fire to include
POST_FIRE_DAYS = 30  # Days after containment to include

In [4]:
in_file = f"../data/California_Historic_Fire_Perimeters.geojson"

In [5]:
fire_gdf = gpd.read_file(in_file)

In [6]:
fire_df = pd.DataFrame(fire_gdf)
fire_df["ALARM_DATE_ISO"] = pd.to_datetime(fire_df.ALARM_DATE, format='%a, %d %b %Y %H:%M:%S %Z').dt.tz_convert('UTC').dt.strftime('%Y-%m-%dT%H:%M:%SZ')
fire_df["CONT_DATE_ISO"]  = pd.to_datetime(fire_df.CONT_DATE, format='%a, %d %b %Y %H:%M:%S %Z').dt.tz_convert('UTC').dt.strftime('%Y-%m-%dT%H:%M:%SZ')

In [ ]:
major_fires = fire_df[
    (fire_df.GIS_ACRES < 10000) &
    (fire_df.DECADES == "2020-January 2025") &
    (fire_df.YEAR_ > 2020.0)
    ].sort_values('GIS_ACRES', ascending=False)

In [13]:
small_fires = fire_df[
    (fire_df.GIS_ACRES < 1000) & 
    (fire_df.GIS_ACRES > 100) & 
    (fire_df.DECADES == "2020-January 2025") &
    (fire_df.ALARM_DATE_ISO.notna()) &
    (fire_df.CONT_DATE_ISO.notna()) ]

In [14]:
small_fires.info()

<class 'pandas.core.frame.DataFrame'>
Index: 361 entries, 3 to 1703
Data columns (total 22 columns):
 #   Column          Non-Null Count  Dtype   
---  ------          --------------  -----   
 0   OBJECTID        361 non-null    int32   
 1   YEAR_           361 non-null    float64 
 2   STATE           361 non-null    object  
 3   AGENCY          361 non-null    object  
 4   UNIT_ID         361 non-null    object  
 5   FIRE_NAME       361 non-null    object  
 6   INC_NUM         361 non-null    object  
 7   ALARM_DATE      361 non-null    object  
 8   CONT_DATE       361 non-null    object  
 9   CAUSE           361 non-null    int32   
 10  C_METHOD        361 non-null    float64 
 11  OBJECTIVE       356 non-null    float64 
 12  GIS_ACRES       361 non-null    float64 
 13  COMMENTS        69 non-null     object  
 14  COMPLEX_NAME    13 non-null     object  
 15  IRWINID         345 non-null    object  
 16  FIRE_NUM        0 non-null      object  
 17  COMPLEX_ID      13 n

In [14]:
top_fires = major_fires.head(5)

In [15]:
analysis_regions = []
for idx, fire in small_fires.iterrows():
    fire_geom = fire.geometry
    buffered_geom = fire_geom.buffer(0.005)  # ~500m buffer around fire
    analysis_regions.append({
        'name': fire.FIRE_NAME,
        'geometry': buffered_geom,
        'alarm_date': fire.ALARM_DATE_ISO,
        'containment_date': fire.CONT_DATE_ISO,
        'acres_burned': fire.GIS_ACRES
    })

In [ ]:
region = analysis_regions[0]
region_gdf = gpd.GeoDataFrame([region], geometry='geometry', crs='EPSG:4326')
region_ee = geemap.geopandas_to_ee(region_gdf)
region_geom = region_ee.geometry()

In [11]:
region_geom.bounds()

ee.Geometry({
  "functionInvocationValue": {
    "functionName": "Geometry.bounds",
    "arguments": {
      "geometry": {
        "functionInvocationValue": {
          "functionName": "Collection.geometry",
          "arguments": {
            "collection": {
              "functionInvocationValue": {
                "functionName": "Collection",
                "arguments": {
                  "features": {
                    "arrayValue": {
                      "values": [
                        {
                          "functionInvocationValue": {
                            "functionName": "Feature",
                            "arguments": {
                              "geometry": {
                                "functionInvocationValue": {
                                  "functionName": "GeometryConstructors.MultiPolygon",
                                  "arguments": {
                                    "coordinates": {
                                      "constantValue": [
                                        [
                                          [
                                            [
                                              -121.54717804056818,
                                              40.06935671044884
                                            ],
                                            [
                                              -121.54725996313525,
                                              40.06980627123728
                                            ],
                                            [
                                              -121.54730009829518,
                                              40.07030073349557
                                            ],
                                            [
                                              -121.54729103690893,
                                              40.070796739188296
                                            ],
                                            [
                                              -121.54723286817813,
                                              40.0712894055609
                                            ],
                                            [
                                              -121.5471261647245,
                                              40.07177388273159
                                            ],
                                            [
                                              -121.54706899633226,
                                              40.07194870830864
                                            ],
                                            [
                                              -121.54710184695894,
                                              40.072260363584135
                                            ],
                                            [
                                              -121.54710628629131,
                                              40.07273886977782
                                            ],
                                            [
                                              -121.54706496214966,
                                              40.07321560891024
                                            ],
                                            [
                                              -121.5469782530431,
                                              40.07368621428198
                                            ],
                                            [
                                              -121.54684695318502,
                                              40.07414637537587
                                            ],
                                            [
                                              -121.54678452869567,
                                              40.074305574850946
                                   

In [16]:
for region in analysis_regions:
    region_gdf = gpd.GeoDataFrame([region], geometry='geometry', crs='EPSG:4326')
    region_ee = geemap.geopandas_to_ee(region_gdf)
    region_geom = region_ee.geometry()
    print(f"Processing region: {region['name']}")

    # Calculate time window for imagery using ISO
    pre_fire_start = ee.Date(region['alarm_date']).advance(-PRE_FIRE_DAYS, 'day')
    post_fire_end = ee.Date(region['containment_date']).advance(POST_FIRE_DAYS, 'day')

    # Get Sentinel-2 collection for this region and time period
    collection = (
        ee.ImageCollection('COPERNICUS/S2_SR_HARMONIZED')
        .filterBounds(region_geom.bounds())
        .filterDate(pre_fire_start, post_fire_end)
        .filter(ee.Filter.lt('CLOUDY_PIXEL_PERCENTAGE', CLOUD_THRESHOLD))
        .select(['B2', 'B3', 'B4', 'B8', 'B11', 'B12'])
    )
    # Create pre-fire and post-fire composites
    pre_fire_img = collection.filterDate(pre_fire_start, ee.Date(region['alarm_date'])).median().clip(region_geom.bounds())
    post_fire_img = collection.filterDate(ee.Date(region['containment_date']), post_fire_end).median().clip(region_geom.bounds())

    # Create fire mask - need to get the original fire geometry
    # First get the original fire geometry (without buffer)
    original_fire_gdf = fire_gdf[fire_gdf.FIRE_NAME == region['name']].iloc[0:1]
    original_fire_fc = geemap.geopandas_to_ee(original_fire_gdf)
    original_fire_geom = original_fire_fc.geometry()
    fire_mask = ee.Image(0).byte().paint(original_fire_fc, 1).rename("mask").clip(region_geom)

    # Calculate NBR
    pre_fire_nbr = pre_fire_img.normalizedDifference(['B8', 'B12']).rename('NBR')
    post_fire_nbr = post_fire_img.normalizedDifference(['B8', 'B12']).rename('NBR')
    dnbr = pre_fire_nbr.subtract(post_fire_nbr).rename('dNBR')

    # Combine all bands into separate images for smaller exports
    clean_name = region['name'].replace(' ', '_').replace('/', '_')
    alarm_date_short = region['alarm_date'][:10].replace('-', '')

    # Export 1: Pre-fire image (only visual bands)
    pre_fire_visual = pre_fire_img.select(['B2', 'B3', 'B4'])  # RGB only
    task1 = ee.batch.Export.image.toDrive(
        image=pre_fire_visual,
        description=f'{clean_name}_{alarm_date_short}',
        folder='data/pre_fire',
        scale=20,
        region=region_geom.bounds(),
        maxPixels=1e10,
        fileFormat='GeoTIFF'
    )
    task1.start()

    # Export 2: Post-fire image (only visual bands)
    post_fire_visual = post_fire_img.select(['B2', 'B3', 'B4'])  # RGB only
    task2 = ee.batch.Export.image.toDrive(
        image=post_fire_visual,
        description=f'{clean_name}_{alarm_date_short}',
        folder='data/post_fire',
        scale=20,
        region=region_geom.bounds(),
        maxPixels=1e10,
        fileFormat='GeoTIFF'
    )
    task2.start()

    # Export 3: Fire mask
    task3 = ee.batch.Export.image.toDrive(
        image=fire_mask,
        description=f'{clean_name}_{alarm_date_short}',
        folder='data/masks',
        scale=20,
        region=region_geom.bounds(),
        maxPixels=1e10,
        fileFormat='GeoTIFF'
    )
    task3.start()

    # Export 4: 
    task4 = ee.batch.Export.image.toDrive(
        image=dnbr,
        description=f'{clean_name}_{alarm_date_short}',
        folder='data/dnbr',
        scale=20,
        region=region_geom.bounds(),
        maxPixels=1e10,
        fileFormat='GeoTIFF'
    )
    task4.start()

Processing region: KENNETH
Processing region: HURST
Processing region: LIDIA
Processing region: DOVE
Processing region: CLEAR
Processing region: FRENCH
Processing region: CANAL
Processing region: CODY
Processing region: LISA
Processing region: GROVE 2
Processing region: ROBLAR
Processing region: CREEK
Processing region: APACHE
Processing region: HERNANDEZ
Processing region: RANCH
Processing region: TULEDAD
Processing region: WATER
Processing region: VALLEY
Processing region: SKY
Processing region: CAMPBELL
Processing region: RECORD
Processing region: DORADO
Processing region: SHEERING
Processing region: STODDARD 3
Processing region: EL PASO
Processing region: POINT
Processing region: BELLA
Processing region: AMORUSO
Processing region: FLYNN
Processing region: HOLIDAY
Processing region: BLUE
Processing region: LUCERNE
Processing region: GLENHAVEN
Processing region: BOGUS
Processing region: POSTA 3
Processing region: BORDER 53
Processing region: PENCIL
Processing region: FELICIA
Processi